In [3]:
import xarray as xr
import cdsapi

In [2]:
client = cdsapi.Client()

2025-03-18 18:00:29,218 INFO [2024-09-26T00:00:00] Watch our [Forum](https://forum.ecmwf.int/) for Announcements, news and other discussed topics.
2025-03-18 18:00:29,220 WARNING [2024-06-16T00:00:00] CDS API syntax is changed and some keys or parameter names may have also changed. To avoid requests failing, please use the "Show API request code" tool on the dataset Download Form to check you are using the correct syntax for your API request.


In [4]:
grid = [0.25, 0.25]
area = [21, -20, 3, 15]  # West Africa 
year = ['{}'.format(y) for y in range(1979, 2025)]
month = ['{:02d}'.format(m) for m in range(1, 13)]

In [6]:
dl_dir = 'tmp/'
out_dir = '../ERA5_WestAfrica/'

## Invariant

In [7]:
filename = 'ERA5_LowRes_Invariant.nc'
dataset = "reanalysis-era5-single-levels-monthly-means"
request = {
    "product_type": ["monthly_averaged_reanalysis"],
    "variable": [
        "geopotential",
        "land_sea_mask"
    ],
    "grid": grid,
    "area": area,
    "year": ["1979"],
    "month": ["01"],
    "time": ["00:00"],
    "data_format": "netcdf",
    "download_format": "unarchived",
}

client.retrieve(dataset, request).download(dl_dir + filename)
print('+++ Done!')

2025-03-18 18:05:10,368 INFO Request ID is 027b8ab2-0ec0-40bc-8f06-f91f0bbbc90f
2025-03-18 18:05:10,454 INFO status has been updated to accepted
2025-03-18 18:05:15,564 WARNING Structural differences in grib fields detected when opening in xarray. Opening the grib file safely, however this may result in files with non-intuitive filenames.
2025-03-18 18:05:15,565 INFO status has been updated to running
2025-03-18 18:05:19,024 INFO status has been updated to successful


2f288ffb224d13a3faf153a7acb4cb94.nc:   0%|          | 0.00/74.8k [00:00<?, ?B/s]

+++ Done!


In [8]:
# Unfortunate necessary cleaning
with xr.open_dataset(dl_dir + filename) as ds:
    # ds = ds.rename({"valid_time": "time"}).drop_vars(["expver", "number"]) #, errors="ignore")
    
    ds = ds.isel(valid_time=0).drop_vars(["expver", "number", "valid_time"])
    ds['orography'] = ds['z']  / 9.80665
    ds['orography'].attrs.update(long_name='Orography', units='m', standard_name='orography')
    ds = ds.drop_vars(["z"])
    ds['lsm'].attrs = {k: v for k, v in ds['lsm'].attrs.items() if not k.startswith("GRIB_")}
    
    ds.attrs = {k: v for k, v in ds.attrs.items() if not k.startswith("GRIB_")}
    ds.to_netcdf(out_dir + filename)

## Temp and precip 

In [9]:
filename = 'ERA5_LowRes_Monthly_t2m.nc'

dataset = "reanalysis-era5-single-levels-monthly-means"
request = {
    "product_type": ["monthly_averaged_reanalysis"],
    "variable": ["2m_temperature"],
    "grid": grid,
    "area": area,
    "year": year,
    "month": month,
    "time": ["00:00"],
    "data_format": "netcdf",
    "download_format": "unarchived",
}

client.retrieve(dataset, request).download(dl_dir + filename)
print('+++ Done!')

2025-03-18 18:05:37,980 INFO Request ID is bc449fde-510d-44dc-8d85-55add8d42f65
2025-03-18 18:05:38,052 INFO status has been updated to accepted
2025-03-18 18:05:43,057 INFO status has been updated to running
2025-03-18 18:06:27,986 WARNING Structural differences in grib fields detected when opening in xarray. Opening the grib file safely, however this may result in files with non-intuitive filenames.
2025-03-18 18:06:27,988 INFO status has been updated to successful


4b7c0eac3542e4a5c89fffd8683553e6.nc:   0%|          | 0.00/9.16M [00:00<?, ?B/s]

+++ Done!


In [10]:
# Unfortunate necessary cleaning
with xr.open_dataset(dl_dir + filename) as ds:
    ds = ds.rename({"valid_time": "time"}).drop_vars(["expver", "number"]) 
     
    ds.attrs = {k: v for k, v in ds.attrs.items() if not k.startswith("GRIB_")}
    for var in ds.variables.keys():
        ds[var].attrs = {k: v for k, v in ds[var].attrs.items() if not k.startswith("GRIB_")}
    
    ds.to_netcdf(out_dir + filename)

In [11]:
filename = 'ERA5_LowRes_Monthly_tp.nc'

dataset = "reanalysis-era5-single-levels-monthly-means"
request = {
    "product_type": ["monthly_averaged_reanalysis"],
    "variable": ["total_precipitation"],
    "grid": grid,
    "area": area,
    "year": year,
    "month": month,
    "time": ["00:00"],
    "data_format": "netcdf",
    "download_format": "unarchived",
}

client.retrieve(dataset, request).download(dl_dir + filename)
print('+++ Done!')

2025-03-18 18:06:30,007 INFO Request ID is 41897274-a13d-455b-a200-68320bcbce58
2025-03-18 18:06:30,087 INFO status has been updated to accepted
2025-03-18 18:06:51,412 INFO status has been updated to running
2025-03-18 18:07:45,806 WARNING Structural differences in grib fields detected when opening in xarray. Opening the grib file safely, however this may result in files with non-intuitive filenames.
2025-03-18 18:07:45,807 INFO status has been updated to successful


2c56659e2512dc2129fb3d4f8e24738d.nc:   0%|          | 0.00/7.58M [00:00<?, ?B/s]

+++ Done!


In [12]:
# Unfortunate necessary cleaning
with xr.open_dataset(dl_dir + filename) as ds:
    ds = ds.rename({"valid_time": "time"}).drop_vars(["expver", "number"]) 
     
    ds.attrs = {k: v for k, v in ds.attrs.items() if not k.startswith("GRIB_")}
    for var in ds.variables.keys():
        ds[var].attrs = {k: v for k, v in ds[var].attrs.items() if not k.startswith("GRIB_")}
    
    ds.to_netcdf(out_dir + filename)